In [1]:
import pyodbc
import pandas as pd
import numpy as np
import os

In [2]:
conn_lims = pyodbc.connect("Driver={SQL Server};"
                        "Server=192.168.5.18\CROPNUT;"
                        "Database=cropnuts;"
                        "uid=thomasTsuma;pwd=GR^KX$uRe9#JwLc6")

In [3]:
commercial = pd.read_sql("select * from Clients where client_Type = 1 and agent_type = 0", con=conn_lims)
farmlab = pd.read_sql("select * from Clients where  client_Type = 6 and agent_type =7", con=conn_lims)
businessPartners = pd.read_sql("select * from Clients where  client_Type = 2 and agent_type = 1 and ParentAgent_id = 0", con=conn_lims)
for col in commercial.columns:
    commercial = commercial.rename(columns={col : col.lower()})
for col in farmlab.columns:
    farmlab = farmlab.rename(columns={col : col.lower()})
for col in businessPartners.columns:
    businessPartners = businessPartners.rename(columns={col : col.lower()})
clients = pd.read_sql("select client_id, client_name from Clients", con=conn_lims)
clients_dict = {}
for i in clients['client_id']:
    name = clients.loc[clients['client_id'] == i]['client_name'].values[0]
    clients_dict[i] = name

C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: 

In [4]:
crops = pd.read_sql("select Crop_Code, Crop_Name from crops", con=conn_lims)
for col in crops.columns:
    crops = crops.rename(columns={col : col.lower()})
crops_dict = {}
for i in crops['crop_code']:
    name = crops.loc[crops['crop_code'] == i]['crop_name'].values[0]
    crops_dict[i] = name

C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [5]:
chemicals = pd.read_sql("select Chemical_Code, Chemical_Symbol from Chemicals", con=conn_lims)
chemicals['Chemical_Symbol'] = [i.strip() for i in chemicals['Chemical_Symbol'].fillna("").values] 
for col in chemicals.columns:
    chemicals = chemicals.rename(columns={col : col.lower()})
chemical_dict = {}
for i in chemicals['chemical_code']:
    symbol = chemicals.loc[chemicals['chemical_code'] == i]['chemical_symbol'].values[0]
    chemical_dict[i] = symbol

C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [6]:
farms = pd.read_sql("SELECT Client_Id, Farm_Name from Farms", con=conn_lims)
for col in farms.columns:
    farms = farms.rename(columns={col : col.lower()})
farm_dict = {}
for i in farms['client_id']:
    name = farms.loc[farms['client_id'] == i]['farm_name'].values[0]
    farm_dict[i] = name

C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [7]:
nutrient = pd.read_sql("Select use_nutrient_req,use_YieldvsSoilTestRanges,crop_code, chemical_code, client_id, Farm_Code from YieldvsSoilTestRangesSettings", con = conn_lims)

C:\Users\Tsuma Thomas\AppData\Roaming\Python\Python310\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [8]:
for col in nutrient.columns:
    if(col == "use_YieldvsSoilTestRanges"):
        continue
    nutrient = nutrient.rename(columns={col : col.lower()})

# Handling Commercial Clients first

In [9]:
commercial_client_nutrient_settings = nutrient.loc[nutrient['client_id'].isin(commercial.client_id)]

In [10]:
commercial_global_nutrient_settings = nutrient.loc[(nutrient['client_id'] == 0) & (nutrient['farm_code'] == 0)]

In [11]:
commercial_client_nutrient_settings['client_type'] = "Commercial"

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1208991636.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  commercial_client_nutrient_settings['client_type'] = "Commercial"


In [12]:
commercial_client_nutrient_settings

use_nutrient_req  use_YieldvsSoilTestRanges  crop_code  chemical_code  \
62              False                      False         23             19   
97              False                       True         69             19   
98              False                       True         69              1   
206             False                       True        702             19   
255             False                       True       1112             19   

     client_id  farm_code client_type  
62         293       6822  Commercial  
97        5528          0  Commercial  
98        5528          0  Commercial  
206       6598          0  Commercial  
255        577          0  Commercial

In [13]:
commercial_global_clients = commercial.loc[~(commercial['client_id'].isin(commercial_client_nutrient_settings.client_id))]

In [14]:
commercial_global_df = pd.DataFrame()

In [15]:
for client in commercial_global_clients.client_id:
    _ = commercial_global_nutrient_settings
    _['client_id'] = client
    _['client_type'] = "Commercial"
    commercial_global_df = pd.concat([commercial_global_df, _])
    

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

...

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "Commercial"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\30612152.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se

In [16]:
commercial_nutrient_settings = pd.concat([commercial_client_nutrient_settings,commercial_global_df])

In [17]:
commercial_nutrient_settings

use_nutrient_req  use_YieldvsSoilTestRanges  crop_code  chemical_code  \
62              False                      False         23             19   
97              False                       True         69             19   
98              False                       True         69              1   
206             False                       True        702             19   
255             False                       True       1112             19   
..                ...                        ...        ...            ...   
417             False                      False       1651              1   
418             False                      False       1650             19   
419             False                      False       1650              1   
420             False                      False       1646             19   
421             False                      False       1646              1   

     client_id  farm_code client_type  
62         293       6822  Commercial  
97        5528          0  Commercial  
98        5528          0  Commercial  
206       6598          0  Commercial  
255        577          0  Commercial  
..         ...        ...         ...  
417      40347          0  Commercial  
418      40347          0  Commercial  
419      40347          0  Commercial  
420      40347          0  Commercial  
421      40347          0  Commercial  

[1479080 rows x 7 columns]

# Handling AgViza Clients

In [18]:
agviza_client_nutrient_settings = nutrient.loc[nutrient['client_id'].isin(businessPartners.client_id)]

In [19]:
agviza_global_nutrient_settings = nutrient.loc[(nutrient['client_id'] == 0) & (nutrient['farm_code'] == 0)]

In [20]:
agviza_client_nutrient_settings['client_type'] = "AgViza"

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\250559802.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  agviza_client_nutrient_settings['client_type'] = "AgViza"


In [21]:
agviza_global_clients = businessPartners.loc[~(businessPartners['client_id'].isin(agviza_client_nutrient_settings.client_id))]

In [22]:
agviza_global_df = pd.DataFrame()

In [23]:
for client in agviza_global_clients.client_id:
    _ = agviza_global_nutrient_settings
    _['client_id'] = client
    _['client_type'] = "AgViza"
    agviza_global_df = pd.concat([agviza_global_df, _])

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1148298261.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1148298261.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "AgViza"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1148298261.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead



In [24]:
agviza_nutrient_settings = pd.concat([agviza_client_nutrient_settings,agviza_global_df])

In [25]:
agviza_nutrient_settings

use_nutrient_req  use_YieldvsSoilTestRanges  crop_code  chemical_code  \
108             False                       True         46             19   
109             False                       True        729             19   
110             False                       True        702             19   
112             False                       True         18             19   
113             False                       True         62             19   
..                ...                        ...        ...            ...   
417             False                      False       1651              1   
418             False                      False       1650             19   
419             False                      False       1650              1   
420             False                      False       1646             19   
421             False                      False       1646              1   

     client_id  farm_code client_type  
108      13318          0      AgViza  
109      13190          0      AgViza  
110      13921          0      AgViza  
112      13190          0      AgViza  
113      14651          0      AgViza  
..         ...        ...         ...  
417      39057          0      AgViza  
418      39057          0      AgViza  
419      39057          0      AgViza  
420      39057          0      AgViza  
421      39057          0      AgViza  

[24018 rows x 7 columns]

# Handling farmlab clients

In [26]:
fl_client_nutrient_settings = nutrient.loc[nutrient['client_id'].isin(farmlab.client_id)]

In [27]:
fl_global_nutrient_settings = nutrient.loc[(nutrient['client_id'] == 0) & (nutrient['farm_code'] == 0)]

In [28]:
fl_client_nutrient_settings['client_type'] = "FarmLab"

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\2082697906.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fl_client_nutrient_settings['client_type'] = "FarmLab"


In [29]:
fl_global_clients = farmlab.loc[~(farmlab['client_id'].isin(fl_client_nutrient_settings.client_id))]

In [30]:
fl_global_df = pd.DataFrame()

In [31]:
for client in fl_global_clients.client_id:
    _ = fl_global_nutrient_settings
    _['client_id'] = client
    _['client_type'] = "FarmLab"
    fl_global_df = pd.concat([fl_global_df, _])

C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1962358813.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_id'] = client
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1962358813.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  _['client_type'] = "FarmLab"
C:\Users\Tsuma Thomas\AppData\Local\Temp\ipykernel_3136\1962358813.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead


In [32]:
fl_nutrient_settings = pd.concat([fl_client_nutrient_settings,fl_global_df])

In [33]:
fl_nutrient_settings

use_nutrient_req  use_YieldvsSoilTestRanges  crop_code  chemical_code  \
0               False                       True        194             19   
1               False                       True        194             19   
2               False                       True         23             19   
3               False                       True         46             19   
4               False                       True         46             19   
..                ...                        ...        ...            ...   
417             False                      False       1651              1   
418             False                      False       1650             19   
419             False                      False       1650              1   
420             False                      False       1646             19   
421             False                      False       1646              1   

     client_id  farm_code client_type  
0         7669          0     FarmLab  
1         7670          0     FarmLab  
2         7669          0     FarmLab  
3         8763          0     FarmLab  
4         7669          0     FarmLab  
..         ...        ...         ...  
417      38912          0     FarmLab  
418      38912          0     FarmLab  
419      38912          0     FarmLab  
420      38912          0     FarmLab  
421      38912          0     FarmLab  

[1807 rows x 7 columns]

In [34]:
final_df = pd.concat([commercial_nutrient_settings, agviza_nutrient_settings, fl_nutrient_settings])

In [35]:
final_df['crop_name'] = final_df['crop_code'].apply(lambda x: crops_dict[x] if x in crops_dict.keys() else "")

In [36]:
final_df['chemical_name'] = final_df['chemical_code'].apply(lambda x: chemical_dict[x] if x in chemical_dict.keys() else "")

In [37]:
final_df

use_nutrient_req  use_YieldvsSoilTestRanges  crop_code  chemical_code  \
62              False                      False         23             19   
97              False                       True         69             19   
98              False                       True         69              1   
206             False                       True        702             19   
255             False                       True       1112             19   
..                ...                        ...        ...            ...   
417             False                      False       1651              1   
418             False                      False       1650             19   
419             False                      False       1650              1   
420             False                      False       1646             19   
421             False                      False       1646              1   

     client_id  farm_code client_type          crop_name chemical_name  
62         293       6822  Commercial                 ma             P  
97        5528          0  Commercial            Tobacco             P  
98        5528          0  Commercial            Tobacco             K  
206       6598          0  Commercial   Potatoes (Irish)             P  
255        577          0  Commercial     Maize (Silage)             P  
..         ...        ...         ...                ...           ...  
417      38912          0     FarmLab   Sorghum (Hybrid)             K  
418      38912          0     FarmLab      Sorghum (OPV)             P  
419      38912          0     FarmLab      Sorghum (OPV)             K  
420      38912          0     FarmLab  Tomatoes (Hybrid)             P  
421      38912          0     FarmLab  Tomatoes (Hybrid)             K  

[1504905 rows x 9 columns]

In [38]:
final_df['client_name'] = final_df['client_id'].apply(lambda x: clients_dict[x] if x in clients_dict.keys() else "")

In [39]:
final_df['farm_name'] = final_df['client_id'].apply(lambda x: farm_dict[x] if x in farm_dict.keys() else "")


In [40]:
final_df.loc[(final_df['use_nutrient_req'] == False) & (final_df['use_YieldvsSoilTestRanges'] == False), 'use_YieldvsSoilTestRanges'] = True

In [43]:
final_df.to_csv("Settings.csv")

In [44]:
final_df

use_nutrient_req  use_YieldvsSoilTestRanges  crop_code  chemical_code  \
62              False                       True         23             19   
97              False                       True         69             19   
98              False                       True         69              1   
206             False                       True        702             19   
255             False                       True       1112             19   
..                ...                        ...        ...            ...   
417             False                       True       1651              1   
418             False                       True       1650             19   
419             False                       True       1650              1   
420             False                       True       1646             19   
421             False                       True       1646              1   

     client_id  farm_code client_type          crop_name chemical_name  \
62         293       6822  Commercial                 ma             P   
97        5528          0  Commercial            Tobacco             P   
98        5528          0  Commercial            Tobacco             K   
206       6598          0  Commercial   Potatoes (Irish)             P   
255        577          0  Commercial     Maize (Silage)             P   
..         ...        ...         ...                ...           ...   
417      38912          0     FarmLab   Sorghum (Hybrid)             K   
418      38912          0     FarmLab      Sorghum (OPV)             P   
419      38912          0     FarmLab      Sorghum (OPV)             K   
420      38912          0     FarmLab  Tomatoes (Hybrid)             P   
421      38912          0     FarmLab  Tomatoes (Hybrid)             K   

                   client_name                  farm_name  
62           Cropnuts Internal            Quality Control  
97   Malawi Fertiliser Company  Malawi Fertilizer Company  
98   Malawi Fertiliser Company  Malawi Fertilizer Company  
206                 Yara Kenya                Yara-Migori  
255       Yara East Africa Ltd                Kiambu Zone  
..                         ...                        ...  
417                    Nigeria                             
418                    Nigeria                             
419                    Nigeria                             
420                    Nigeria                             
421                    Nigeria                             

[1504905 rows x 11 columns]

Empty DataFrame
Columns: [use_nutrient_req, use_YieldvsSoilTestRanges, crop_code, chemical_code, client_id, farm_code, client_type, crop_name, chemical_name, client_name, farm_name]
Index: []